In [1]:
print("Hii")

Hii


In [2]:
%pwd

'd:\\mental-bot\\mental-health-chatbot\\research'

In [3]:
import os
os.chdir("../")

In [4]:
%pwd

'd:\\mental-bot\\mental-health-chatbot'

In [5]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

c:\Users\shubh\.conda\envs\menhel\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:
#Extract text from pdf files
def load_pdf_files(data):
    loader = DirectoryLoader(
        data,
        glob="*.pdf",
        loader_cls=PyPDFLoader
    )

    documents = loader.load()
    return documents
    

In [9]:
extracted_data = load_pdf_files("data")

In [10]:
extracted_data

[Document(metadata={'producer': 'iTextSharp 5.1.2 (c) 1T3XT BVBA', 'creator': 'PyPDF', 'creationdate': '2015-11-28T10:55:22+02:00', 'author': 'Len Sperry', 'moddate': '2017-10-02T19:35:03+02:00', 'pxcviewerinfo': "PDF-XChange Viewer;2.5.201.0 [V5];May  7 2012;10:54:34;D:20170906161517+04'00'", 'title': 'Mental Health and Mental Disorders', 'ebx_publisher': 'ABC-CLIO', 'source': 'data\\Mental Health book.pdf', 'total_pages': 1443, 'page': 0, 'page_label': 'Cover'}, page_content=''),
 Document(metadata={'producer': 'iTextSharp 5.1.2 (c) 1T3XT BVBA', 'creator': 'PyPDF', 'creationdate': '2015-11-28T10:55:22+02:00', 'author': 'Len Sperry', 'moddate': '2017-10-02T19:35:03+02:00', 'pxcviewerinfo': "PDF-XChange Viewer;2.5.201.0 [V5];May  7 2012;10:54:34;D:20170906161517+04'00'", 'title': 'Mental Health and Mental Disorders', 'ebx_publisher': 'ABC-CLIO', 'source': 'data\\Mental Health book.pdf', 'total_pages': 1443, 'page': 1, 'page_label': '1-i'}, page_content='Mental Health and  \nMental Diso

In [11]:
len(extracted_data)

1443

In [12]:
from typing import List
from langchain.schema import Document

def filer_to_minimal_docs(docs: List[Document]) -> List[Document]:
    minimal_docs: List[Document] = []
    for doc in docs:
        src = doc.metadata.get("source")
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={"source": src} if src else {}
            )
        )
    return minimal_docs

In [13]:
minimal_docs = filer_to_minimal_docs(extracted_data)

In [14]:
minimal_docs

[Document(metadata={'source': 'data\\Mental Health book.pdf'}, page_content=''),
 Document(metadata={'source': 'data\\Mental Health book.pdf'}, page_content='Mental Health and  \nMental Disorders'),
 Document(metadata={'source': 'data\\Mental Health book.pdf'}, page_content='This page intentionally left blank'),
 Document(metadata={'source': 'data\\Mental Health book.pdf'}, page_content='Mental Health and \nMental Disorders\nAN ENCYCLOPEDIA OF CONDITIONS, \nTREATMENTS, AND WELL-BEING\nVolume 1: A–E\nLEN SPERRY\nEDITOR-IN-CHIEF\nAssociate Editors\nALEXANDRA CUNNINGHAM\nMELISSA A. MARIANI\nMINDY PARSONS\nSTEVEN R. VENSEL'),
 Document(metadata={'source': 'data\\Mental Health book.pdf'}, page_content='Copyright © 2016 by ABC-CLIO, LLC\nAll rights reserved. No part of this publication may be reproduced, stored in a retrieval \nsystem, or transmitted, in any form or by any means, electronic, mechanical,  \nphotocopying, recording, or otherwise, except for the inclusion of brief quotations in

In [15]:
#Split the documents into smaller chunks
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size=500,
        chunk_overlap=20,
    )
    text_chunk = text_splitter.split_documents(minimal_docs)
    return text_chunk

In [16]:
text_chunk = text_split(minimal_docs)
print(f"Number of text chunks: {len(text_chunk)}")

Number of text chunks: 11736


In [17]:
from langchain.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name
    )
    return embeddings

embedding = download_embeddings()


C:\Users\shubh\AppData\Local\Temp\ipykernel_21492\198388822.py:5: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(


In [18]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [19]:
vector = embedding.embed_query("Hello world")
vector

[-0.03447727859020233,
 0.031023195013403893,
 0.0067350007593631744,
 0.02610897831618786,
 -0.03936203941702843,
 -0.16030246019363403,
 0.06692393869161606,
 -0.006441489793360233,
 -0.04745043069124222,
 0.014758850447833538,
 0.07087530940771103,
 0.05552756413817406,
 0.019193332642316818,
 -0.026251299306750298,
 -0.010109570808708668,
 -0.026940522715449333,
 0.022307388484477997,
 -0.022226659581065178,
 -0.1496925801038742,
 -0.017493056133389473,
 0.00767620699480176,
 0.05435231328010559,
 0.003254441311582923,
 0.03172589838504791,
 -0.08462132513523102,
 -0.02940601296722889,
 0.0515955425798893,
 0.048124007880687714,
 -0.003314810572192073,
 -0.05827917903661728,
 0.04196931794285774,
 0.022210605442523956,
 0.12818878889083862,
 -0.022338947281241417,
 -0.011656264774501324,
 0.06292837113142014,
 -0.03287631645798683,
 -0.09122605621814728,
 -0.031175334006547928,
 0.052699584513902664,
 0.04703482240438461,
 -0.0842030793428421,
 -0.030056186020374298,
 -0.0207448396

In [20]:
print(len(vector))

384


In [21]:
from dotenv import load_dotenv
import os
load_dotenv()

True

In [27]:
PINECONE_API_KEY = os.getenv("PINECONE_API_KEY")
GEMINI_API_KEY = os.getenv("GEMINI_API_KEY")

os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY
os.environ["GEMINI_API_KEY"] = GEMINI_API_KEY

In [28]:
from pinecone import Pinecone
pinecone_api_key = PINECONE_API_KEY

pc=Pinecone(api_key=pinecone_api_key)

In [29]:
from pinecone import ServerlessSpec

index_name="mental-health-chatbot"

if not pc.has_index(index_name):
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws", region="us-east-1")
    )

index = pc.Index(index_name)

In [30]:
from langchain_pinecone import PineconeVectorStore

docsearch=PineconeVectorStore.from_documents(
    documents=text_chunk,
    embedding=embedding,
    index_name=index_name
)

In [31]:
from langchain_pinecone import PineconeVectorStore

docsearch=PineconeVectorStore.from_existing_index(
    embedding=embedding,
    index_name=index_name
)

In [32]:
retriver = docsearch.as_retriever(search_type="similarity", search_kwargs={"k":3})

In [33]:
retrived_docs = retriver.invoke("How to deal with depression?")
retrived_docs

[Document(id='16c10ca4-0afb-4f1d-85e4-8883bea6bebf', metadata={'source': 'data\\Mental Health book.pdf'}, page_content='reduction.\nDescription\n“Depression” is the general name for a group of men-\ntal conditions known as depressive disorders. Most \nindividuals experience depressive symptoms (feeling \ndown or blue) at some point in their lives. When these \nsymptoms are mild and short lived, they are considered \na normal emotional reaction. However, when they are \nmore severe and significantly affect daily functioning, \nthey are considered a depressive disorder. Depressive'),
 Document(id='945e3b1a-8b1e-4fa1-9523-754a4321b583', metadata={'source': 'data\\Mental Health book.pdf'}, page_content='depressant.\nDepression is an emotional state characterized by feelings of sadness, low self-esteem, guilt, \nor reduced ability to enjoy life. It is not considered a mental disorder unless it signifi-\ncantly disrupts one’s daily functioning.\nDepressive disorders are a group of mental dis

In [34]:
from langchain_google_genai import ChatGoogleGenerativeAI

chatModel = ChatGoogleGenerativeAI(model="gemini-2.5-pro", google_api_key=GEMINI_API_KEY)

c:\Users\shubh\.conda\envs\menhel\lib\site-packages\google\api_core\_python_version_support.py:266: FutureWarning: You are using a Python version (3.10.19) which Google will stop supporting in new releases of google.api_core once it reaches its end of life (2026-10-04). Please upgrade to the latest Python version, or at least Python 3.11, to continue receiving updates for google.api_core past that date.
  warnings.warn(message, FutureWarning)


In [35]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [42]:
system_prompt = (
    "You are a compassionate and knowledgeable mental health assistant. "
    "Your role is to support users by providing helpful, empathetic, and "
    "psychologically safe responses. Use the following retrieved context "
    "to answer their questions or offer emotional support. "
    "If you are not sure about something or it seems beyond your capability, "
    "gently encourage the user to reach out to a licensed mental health professional. "
    "Keep your responses warm, understanding, and concise."
    "\n\n"
    "{context}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system", system_prompt),
        ("human", "{input}"),
    ]
)


In [43]:
question_answer_chain = create_stuff_documents_chain(chatModel, prompt)
rag_chain = create_retrieval_chain(retriver, question_answer_chain)

In [44]:
response = rag_chain.invoke({"input": "what is depression?"})
print(response["answer"])

Thank you for asking such an important question. It's helpful to understand what we mean when we talk about depression.

Based on the information I have, depression is more than just feeling sad. While most of us feel "down or blue" at times, which is a normal emotional reaction, a depressive disorder is different.

It's a mental health condition characterized by persistent feelings of sadness, a loss of interest in things you once enjoyed, and other emotional and physical problems. It can also involve:

*   Changes in sleep or appetite
*   Loss of concentration
*   Feelings of low self-esteem or guilt

The key difference is that a depressive disorder is severe enough to significantly disrupt your daily life and functioning.

If any of this sounds familiar, please know that you're not alone. It can be incredibly helpful to talk with a licensed mental health professional who can offer guidance and support. Please take care.
